In [1]:
import sys
sys.path
sys.path.append('c:\\users\\dell\\appdata\\local\\programs\\python\\python310\\lib\\site-packages')
sys.path.append('c:\\users\\dell\\appdata\\local\\programs\\python\\python310\\scripts ')
# sys.path.append('C:\\Users\\dell\\AppData\\Roaming\\nltk_data')
import pandas as pd
import numpy as np
import nltk
import re
import string
import csv
import nltk
from nameparser.parser import HumanName
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords
from nltk.corpus import wordnet
import numpy.linalg as LA
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.tokenize import RegexpTokenizer
from nltk.stem.lancaster import LancasterStemmer
from nltk.stem import PorterStemmer
from autocorrect import Speller
import datefinder
from num2words import num2words
from sklearn.metrics import precision_score, recall_score, f1_score
from sklearn.metrics import classification_report
import scipy.sparse
from pprint import pprint
person_names = []
from gensim import interfaces, utils, matutils
import gensim
import gensim.corpora as corpora
from gensim.models import CoherenceModel# spaCy for preprocessing
import spacy


In [2]:
cisi_text = ""
f1 = open('E:\\python\\cisi.txt', 'r')
for line in f1:
    cisi_text = cisi_text + line
cisi_corpus = cisi_text.split('\n')

cacm_text= ""
f2 = open('E:\\python\\cacm.txt', 'r')
for line in f2:
    cacm_text = cacm_text + line
cacm_corpus = cacm_text.split('\n')

In [3]:
cisi_dictionary = {
    '.I': [],
    '.C' : [],
    '.X' : []
}
cacm_dictionary = {
    '.I': [],
    '.C' : [],
    '.X' : []
}

In [4]:
def cisi_to_chunk(chunk):
    global person_names
    for sentence in chunk.split('\n'):
        if ".I" in sentence:
            start_index=chunk.find(".I")
            lword=len(".I")
            extracted_string= chunk[start_index:start_index+lword]
            required_string_index = chunk.index(extracted_string)+2
            required_string= chunk[required_string_index:chunk.find(".T")]
            cisi_dictionary[".I"].append(required_string)
        if ".T" in sentence:
            start_index=chunk.find(".T")
            lword=len(".T")
            extracted_string= chunk[start_index:start_index+lword]
            required_string_index = chunk.index(extracted_string)+2
            required_string= chunk[required_string_index:chunk.find(".X")]
            cisi_dictionary[".C"].append(required_string)
        if ".A" in sentence:
            start_index=chunk.find(".A")
            lword=len(".A")
            extracted_string= chunk[start_index:start_index+lword]
            required_string_index = chunk.index(extracted_string)+3
            required_string= chunk[required_string_index:chunk.find(".W")]
            person_names.append(required_string)
        if ".X" in sentence:
            start_index=chunk.find(".X")
            lword=len(".X")
            extracted_string= chunk[start_index:start_index+lword]
            required_string_index = chunk.index(extracted_string)+3
            required_string= chunk[required_string_index:chunk.find("\n.I")]
            cisi_dictionary[".X"].append(required_string)

In [5]:
isThereAnI = True
chunks_list = [None] * 1500
i = 0
for sentence in cisi_corpus:
    if ".I " in sentence:
        if isThereAnI:
            chunks_list[i]= ' '
            isThereAnI = False
        else:
            cisi_to_chunk(chunks_list[i])
            i = i + 1
            chunks_list[i] = ' '
    chunks_list[i] = chunks_list[i] + sentence + ' '


In [6]:
cisi_df = pd.DataFrame(data=cisi_dictionary)
# pd.set_option('max_columns', 5)
pd.set_option('max_colwidth', 10000)
cisi_df.columns = ['id','content','references']
cisi_df 

id  \
0         1    
1         2    
2         3    
3         4    
4         5    
...      ...   
1455   1456    
1456   1457    
1457   1458    
1458   1459    
1459   1460    

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  content  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       18 Editions of the Dewey Decimal Classifications .A Comaromi, J.P. .W    The present study is a history of the DEWEY Decimal Classification.  The first edition of the DDC was published in 1876, the eighteenth edition in 1971, and future editions will continue to appear as needed.  In spite of the DDC's long and healthy life, however, its full story has never been told.  There have been biographies of Dewey that briefly describe his system, but this is the first attempt to provide a detailed history of the work that more than any other has spurred the growth of librarianship in this country and abroad.    
1                                                                                                 Use Made of Technical Libraries .A  Slater, M. .W This report is an analysis of 6300 acts of use in 104 technical libraries in the United Kingdom. Library use is only one aspect of the wider pattern of information use.  Information transfer in libraries is restricted to the use of documents.  It takes no account of documents used outside the library, still less of information transferred orally from person to person.  The library acts as a channel in only a proportion of the situations in which information is transferred. Taking technical information transfer as a whole, there is no doubt that this proportion is not the major one.  There are users of technical information - particularly in technology rather than science - who visit libraries rarely if at all, relying on desk collections of handbooks, current periodicals and personal contact with their colleagues and with people in other organizations.  Even regular library users also receive information in other ways.    
2                                                                                                                                                                                                                                                                                           Two Kinds of Power An Essay on Bibliographic Control .A Wilson, P. .W     The relationships between the organization and control of writings and the organization and control of knowledge and information will inevitably enter our story, for writings contain, along with much else

In [56]:
cisi_df.content.loc[0]

'two thousand and twenty-two edit dewey decim classif comaromi present studi histori dewey decim classif edit ddc publish one thousand , eight hundr and seventy-six eighteenth futur edit continu need spite ddc long healthi life full stori tell biographi dewey briefli describ system attempt provid detail histori work spur growth librarianship countri abroad '

In [20]:
def cacm_to_chunk(chunk):
    global person_names
    for sentence in chunk.split('\n'):
        if ".I" in sentence:
            start_index=chunk.find(".I")
            lword=len(".I")
            extracted_string= chunk[start_index:start_index+lword]
            required_string_index = chunk.index(extracted_string)+2
            required_string= chunk[required_string_index:chunk.find(".T")]
            cacm_dictionary[".I"].append(required_string)
        if ".T" in sentence:
            start_index=chunk.find(".T")
            lword=len(".T")
            extracted_string= chunk[start_index:start_index+lword]
            required_string_index = chunk.index(extracted_string)+2
            required_string= chunk[required_string_index:chunk.find(".N")]
            cacm_dictionary[".C"].append(required_string)
        if ".A" in sentence:
            start_index=chunk.find(".A")
            lword=len(".A")
            extracted_string= chunk[start_index:start_index+lword]
            required_string_index = chunk.index(extracted_string)+3
            required_string= chunk[required_string_index:chunk.find(".N")]
#             cacm_dictionary[".C"].append(required_string)
            person_names.append(required_string)
        if ".X" in sentence:
            start_index=chunk.find(".X")
            lword=len(".X")
            extracted_string= chunk[start_index:start_index+lword]
            required_string_index = chunk.index(extracted_string)+3
            required_string= chunk[required_string_index:chunk.find("\n.I")]
            cacm_dictionary[".X"].append(required_string)

In [21]:
isThereAnI = True
chunks_list = [None] * 3300
i = 0
for sentence in cacm_corpus:
    if ".I " in sentence:
        if isThereAnI:
            chunks_list[i]= ' '
            isThereAnI = False
        else:
            cacm_to_chunk(chunks_list[i])
            i = i + 1
            chunks_list[i] = ' '
    chunks_list[i] = chunks_list[i] + sentence + ' '

In [22]:
cacm_df = pd.DataFrame(data=cacm_dictionary)
pd.set_option('max_colwidth', 10000)
cacm_df.columns = ['id','content','references']
cacm_df 

id  \
0         1    
1         2    
2         3    
3         4    
4         5    
...      ...   
3198   3199    
3199   3200    
3200   3201    
3201   3202    
3202   3203    

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               content  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             Preliminary Report-International Algebraic Language .B CACM December, 1958 .A Perlis, A. J. Samelson,K.    
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              Extraction of Roots by Repeated Subtractions for Digital Computers .B CACM December, 1958 .A Sugai, I.    
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           Techniques Department on Matrix Program Schemes .B CACM December, 1958 .A Friedman, M. D.    
3                                                                                                                                

In [7]:
#first round cleaning
#defining the names
person_list = []
persons = person_list
def clean_text_round1(text):
    global person_names
    tokens = nltk.tokenize.word_tokenize(text)
    pos = nltk.pos_tag(tokens)
    sentt = nltk.ne_chunk(pos, binary = False)
    person = []
    name = ""
    for subtree in sentt.subtrees(filter=lambda t: t.label() == 'PERSON'):
        for leaf in subtree.leaves():
            person.append(leaf[0])
        if len(person) > 1: #avoid grabbing lone surnames
            for part in person:
                name += part + ' '
            if name[:-1] not in person_list:
                person_list.append(name[:-1])
            name = ''
        person = []
    for person in person_list:
        person_split = person.split(" ")
        for name in person_split:
            if wordnet.synsets(name):
                if(name in person):
                    persons.remove(person)
                    break
    person_names = person_names + persons
#     print(person_names)
    return text
round1 = lambda x: clean_text_round1(x)

In [8]:
#second cleaning round
#cleaning the additional \n and \t
#Apply a second round of text cleaning techniques
tokenizer = RegexpTokenizer(r'\w+')
stop_words = set(stopwords.words('english'))
commom_words = open('C:\\Users\\dell\\Desktop\\common_words.txt', 'r').read().split()

def clean_text_round2(text):
    new_text = ' '
    text = text.lower()
    text = re.sub('[''""_]',' ',text)
    text = re.sub('\t',' ',text)
    text = re.sub('\n',' ',text)
    text = re.sub('[%s]' % re.escape(string.punctuation), ' ',text)
    word_tokens = word_tokenize(text)
    for w in word_tokens:
#         print(w)
        if w not in commom_words and w not in stop_words:
            new_text = new_text + w +' '
    return new_text
round2 = lambda x: clean_text_round2(x)

In [9]:
#third cleaning round
#working on auto correct
def contain_in_names_list(name):
    found = False
    for person_name in person_names:
        if person_name.find(name) != -1:
            found = True
    return found

def clean_text_round3(text):
    new_text = ''
    words = word_tokenize(text)
    spell = Speller(lang='en')
    for w in words:
        if(not contain_in_names_list(w)):
            w = spell(w)
            new_text += w + ' '
        else:
            new_text += w + ' '
    return new_text
round3 = lambda x: clean_text_round3(x)

In [10]:
#forth cleaning round
#working on dates finding
def clean_text_round4(text):
    text = sent_tokenize(text)
    required_text = ""
    for sentence in text:
        matches = datefinder.find_dates(sentence,source = True)
        if matches is not None:
            try:
                for match in matches:
                    required_year = match[0].year
                    required_date =str(required_year)
                    temp_date = match[1]
                    sentence = sentence.replace(temp_date,required_date,1)
            except:
                print("error with date")
        required_text = required_text + sentence
    return required_text
round4 = lambda x: clean_text_round4(x)

In [11]:
#fifth cleaning round
#Apply lemmitization round of text cleaning techniques
#which is from parallel to singular
def clean_text_round5(text):
    new_text = ''
    lemma = nltk.wordnet.WordNetLemmatizer()
    words = word_tokenize(text)
    for w in words:
        w=lemma.lemmatize(w,pos='v')
        w = lemma.lemmatize(w)
        new_text += w + ' '
    return new_text
round5 = lambda x: clean_text_round5(x)

In [12]:
def clean_text_round6(text):
    new_text = ''
    words = word_tokenize(text)
    for w in words:
        if w.isnumeric():
            w = num2words(int(w))
        if(re.search(r'\d',w)):
            w = ' '
        new_text += w + ' ' 
    return new_text
round6 = lambda x: clean_text_round6(x)

In [13]:
#sixth cleaning round
#Apply Stemming round of text cleaning techniques
#which is from past to current verbs

def clean_text_round7(text):
    ps = PorterStemmer()
    new_text = ''
    words = word_tokenize(text)
    for w in words:
        w = ps.stem(w)
        new_text += w + ' '
    return new_text
round7 = lambda x: clean_text_round7(x)

In [14]:
# cisi_df.content = cisi_df.content.apply(round1)
cisi_df.content = cisi_df.content.apply(round2)
# cisi_df.content = cisi_df.content.apply(round3)
cisi_df.content = cisi_df.content.apply(round4)
cisi_df.content = cisi_df.content.apply(round5)
cisi_df.content = cisi_df.content.apply(round6)
cisi_df.content = cisi_df.content.apply(round7)
cisi_df

error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date


id  \
0         1    
1         2    
2         3    
3         4    
4         5    
...      ...   
1455   1456    
1456   1457    
1457   1458    
1458   1459    
1459   1460    

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              content  \
0                                                                                                                                                                                                              two thousand and twenty-two edit dewey decim classif comaromi present studi histori dewey decim classif edit ddc publish one thousand , eight hundr and seventy-six eighteenth futur edit continu need spite ddc long healthi life full stori tell biographi dewey briefli describ system attempt provid detail histori work spur growth librarianship countri abroad    
1                                  make technic librari slater report analysi six thousand , three hundr act one hundr and four technic librari unit kingdom librari aspect wider pattern inform inform transfer librari restrict document take account document librari inform transfer oral person person librari act channel proport situat inform transfer take technic inform transfer doubt proport major user technic inform technolog scienc visit librari rare reli desk collect handbook period person contact colleagu peopl organ regular librari user receiv inform way    
2                                                                                                                     kind power essay bibliograph control wilson relationship organ control write organ control knowledg inform inevit enter stori write great deal mankind stock knowledg inform bibliograph control form power knowledg form power familiar slogan claim bibliograph control sens power power power obtain knowledg record write form write simpli simpl storehous knowledg satisfactorili discu bibliograph control simpli control knowledg inform contain write    
3                                                                                                                                system analysi univers librari final report research project buckland establish univers one thousand , nine hundr and sixti provok highli stimul examin natur purpos manag academ librari long establish attitud method question make basic difficulti remain lack object inform way provid librari servic univers report ugc committe librari parri repot two hundr and sixty-seven gener endors stress need research aspect academ librari provis    
4     librari manag game report research project brophi game profession educ widespread decad method number field hundr year origin trace simpl war game militari train real thing unavail danger recent time game sophist larg electron comput handl complex calcul involv one thousand , nine hundr and fifty-six develop manag game introduc techniqu spread rapidli wide varieti disciplin today level educ primari school class cours experi profession men woman main game explos rapid develop sophist manag techniqu simul mathemat model make rapid advanc comput technolog    
...                                                                                                                                                                                                                                                                                                                                                                                                                

In [15]:
vectorizer = TfidfVectorizer() 
vectors = vectorizer.fit_transform(cisi_df.content)
columns = vectorizer.get_feature_names()
data_dtm_2 = pd.DataFrame(vectors.todense(),columns = columns)
pd.set_option('max_colwidth', 100)
pd.set_option('max_columns', 10000)
data_dtm_2

aacr  abandon  abbot  abbrevi  aberrystwyth  abidjan  abil  abl  abli  \
0      0.0      0.0    0.0      0.0           0.0      0.0   0.0  0.0   0.0   
1      0.0      0.0    0.0      0.0           0.0      0.0   0.0  0.0   0.0   
2      0.0      0.0    0.0      0.0           0.0      0.0   0.0  0.0   0.0   
3      0.0      0.0    0.0      0.0           0.0      0.0   0.0  0.0   0.0   
4      0.0      0.0    0.0      0.0           0.0      0.0   0.0  0.0   0.0   
...    ...      ...    ...      ...           ...      ...   ...  ...   ...   
1455   0.0      0.0    0.0      0.0           0.0      0.0   0.0  0.0   0.0   
1456   0.0      0.0    0.0      0.0           0.0      0.0   0.0  0.0   0.0   
1457   0.0      0.0    0.0      0.0           0.0      0.0   0.0  0.0   0.0   
1458   0.0      0.0    0.0      0.0           0.0      0.0   0.0  0.0   0.0   
1459   0.0      0.0    0.0      0.0           0.0      0.0   0.0  0.0   0.0   

      abno  abnorm  abolish  abort  about  abrad  abraham  abreast  abridg  \
0      0.0     0.0      0.0    0.0    0.0    0.0      0.0      0.0     0.0   
1      0.0     0.0      0.0    0.0    0.0    0.0      0.0      0.0     0.0   
2      0.0     0.0      0.0    0.0    0.0    0.0      0.0      0.0     0.0   
3      0.0     0.0      0.0    0.0    0.0    0.0      0.0      0.0     0.0   
4      0.0     0.0      0.0    0.0    0.0    0.0      0.0      0.0     0.0   
...    ...     ...      ...    ...    ...    ...      ...      ...     ...   
1455   0.0     0.0      0.0    0.0    0.0    0.0      0.0      0.0     0.0   
1456   0.0     0.0      0.0    0.0    0.0    0.0      0.0      0.0     0.0   
1457   0.0     0.0      0.0    0.0    0.0    0.0      0.0      0.0     0.0   
1458   0.0     0.0      0.0    0.0    0.0    0.0      0.0      0.0     0.0   
1459   0.0     0.0      0.0    0.0    0.0    0.0      0.0      0.0     0.0   

        abroad  absenc  absent  absolut  absorpt  abstract  abstractli  \
0     0.157559     0.0     0.0      0.0      0.0  0.000000         0.0   
1     0.000000     0.0     0.0      0.0      0.0  0.000000         0.0   
2     0.000000     0.0     0.0      0.0      0.0  0.000000         0.0   
3     0.000000     0.0     0.0      0.0      0.0  0.000000         0.0   
4     0.000000     0.0     0.0      0.0      0.0  0.000000         0.0   
...        ...     ...     ...      ...      ...       ...         ...   
1455  0.000000     0.0     0.0      0.0      0.0  0.000000         0.0   
1456  0.000000     0.0     0.0      0.0      0.0  0.000000         0.0   
1457  0.000000     0.0     0.0      0.0      0.0  0.000000         0.0   
1458  0.000000     0.0     0.0      0.0      0.0  0.120132         0.0   
1459  0.000000     0.0     0.0      0.0      0.0  0.000000         0.0   

      abstractor  abstrus  absurd  abund  abundantli   ac    academ  academi  \
0            0.0      0.0     0.0    0.0         0.0  0.0  0.000000      0.0   
1            0.0      0.0     0.0    0.0         0.0  0.0  0.000000      0.0   
2            0.0      0.0     0.0    0.0         0.0  0.0  0.000000      0.0   
3            0.0      0.0     0.0    0.0         0.0  0.0  0.217847      0.0   
4            0.0      0.0     0.0    0.0         0.0  0.0  0.000000      0.0   
...          ...      ...     ...    ...         ...  ...       ...      ...   
1455         0.0      0.0     0.0    0.0         0.0  0.0  0.000000      0.0   
1456         0.0      0.0     0.0    0.0         0.0  0.0  0.000000      0.0   
1457         0.0      0.0     0.0    0.0         0.0  0.0  0.000000      0.0   
1458         0.0      0.0     0.0    0.0         0.0  0.0  0.000000      0.0   
1459         0.0      0.0     0.0    0.0         0.0  0.0  0.000000      0.0   

      academia  academician  accademia  acceler  accentu  accept  access  \
0          0.0          0.0        0.0      0.0      0.0     0.0     0.0   
1          0.0          0.0        0.0      0.0      0.0     0.0     0.0   
2          0.0          0.0        0.0    

In [32]:
cacm_df.content = cacm_df.content.apply(round1)
cacm_df.content = cacm_df.content.apply(round2)
# cacm_df.content = cacm_df.content.apply(round3)
cacm_df.content = cacm_df.content.apply(round4)
cacm_df.content = cacm_df.content.apply(round5)
cacm_df.content = cacm_df.content.apply(round6)
cacm_df.content = cacm_df.content.apply(round7)
cacm_df

error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date


id  \
0         1    
1         2    
2         3    
3         4    
4         5    
...      ...   
3198   3199    
3199   3200    
3200   3201    
3201   3202    
3202   3203    

                                                                                                  content  \
0     preliminari report intern algebra languag cacm one thousand , nine hundr and fifty-eight perli s...   
1         extract root repeat subtract digit comput cacm one thousand , nine hundr and fifty-eight sugai    
2                                                             techniqu depart matrix program scheme cacm    
3                glossari comput engin program terminolog cacm one thousand , nine hundr and fifty-eight    
4                               squar root approxim cacm one thousand , nine hundr and fifty-eight wadey    
...                                                                                                   ...   
3198  algem algebra manipul algem packag subprogram write slip fortran iv map seven thousand and ninet...   
3199  formac program solut linear boundari initi problem comput program develop obtain approxim solut ...   
3200  symbol manipul poisson seri poisson seri variabl manag symbol set formal subroutin write partial...   
3201  manip comput system algebra analyt differenti mathemat express oper write fortran notat store co...   
3202  grad assist program symbol algebra manipul differenti gener recurs algebra differenti assist gra...   

                                                                                               references  
0     100\t5\t1 123\t5\t1 164\t5\t1 1\t5\t1 1\t5\t1 1\t5\t1 205\t5\t1 210\t5\t1 214\t5\t1 1982\t5\t1 3...  
1                                                                                 2\t5\t2 2\t5\t2 2\t5\t2  
2                                                                                 3\t5\t3 3\t5\t3 3\t5\t3  
3                                                                                 4\t5\t4 4\t5\t4 4\t5\t4  
4                                                                                 5\t5\t5 5\t5\t5 5\t5\t5  
...                                                                                                   ...  
3198  1396\t5\t3199 3199\t5\t3199 3199\t5\t3199 3199\t5\t3199 964\t6\t3199 1028\t6\t3199 1029\t6\t3199...  
3199  1396\t5\t3200 3200\t5\t3200 3200\t5\t3200 3200\t5\t3200 964\t6\t3200 1028\t6\t3200 1029\t6\t3200...  
3200  1396\t5\t3201 3201\t5\t3201 3201\t5\t3201 3201\t5\t3201 964\t6\t3201 1028\t6\t3201 1029\t6\t3201...  
3201  1396\t5\t3202 3202\t5\t3202 3202\t5\t3202 3202\t5\t3202 964\t6\t3202 1028\t6\t3202 1029\t6\t3202...  
3202  1396\t5\t3203 3203\t5\t3203 3203\t5\t3203 3203\t5\t3203 964\t6\t3203 1028\t6\t3203 1029\t6\t3203...  

[3203 rows x 3 columns]

In [33]:
vectorizer = TfidfVectorizer() 
cacm_vectors = vectorizer.fit_transform(cacm_df.content)
data_dtm_cacm = pd.DataFrame(cacm_vectors.todense(),columns = vectorizer.get_feature_names())
pd.set_option('max_colwidth', 100)
pd.set_option('max_columns', 10000)
data_dtm_cacm

aaron  abac  abacu  abandon  abbott  abbrevi  abcd       abd  abdali  \
0       0.0   0.0    0.0      0.0     0.0      0.0   0.0  0.000000     0.0   
1       0.0   0.0    0.0      0.0     0.0      0.0   0.0  0.000000     0.0   
2       0.0   0.0    0.0      0.0     0.0      0.0   0.0  0.000000     0.0   
3       0.0   0.0    0.0      0.0     0.0      0.0   0.0  0.000000     0.0   
4       0.0   0.0    0.0      0.0     0.0      0.0   0.0  0.000000     0.0   
...     ...   ...    ...      ...     ...      ...   ...       ...     ...   
3198    0.0   0.0    0.0      0.0     0.0      0.0   0.0  0.000000     0.0   
3199    0.0   0.0    0.0      0.0     0.0      0.0   0.0  0.000000     0.0   
3200    0.0   0.0    0.0      0.0     0.0      0.0   0.0  0.000000     0.0   
3201    0.0   0.0    0.0      0.0     0.0      0.0   0.0  0.000000     0.0   
3202    0.0   0.0    0.0      0.0     0.0      0.0   0.0  0.162521     0.0   

      abel  abelian  aberth  abil  abl  abraham  abram  abramowich  abscissa  \
0      0.0      0.0     0.0   0.0  0.0      0.0    0.0         0.0       0.0   
1      0.0      0.0     0.0   0.0  0.0      0.0    0.0         0.0       0.0   
2      0.0      0.0     0.0   0.0  0.0      0.0    0.0         0.0       0.0   
3      0.0      0.0     0.0   0.0  0.0      0.0    0.0         0.0       0.0   
4      0.0      0.0     0.0   0.0  0.0      0.0    0.0         0.0       0.0   
...    ...      ...     ...   ...  ...      ...    ...         ...       ...   
3198   0.0      0.0     0.0   0.0  0.0      0.0    0.0         0.0       0.0   
3199   0.0      0.0     0.0   0.0  0.0      0.0    0.0         0.0       0.0   
3200   0.0      0.0     0.0   0.0  0.0      0.0    0.0         0.0       0.0   
3201   0.0      0.0     0.0   0.0  0.0      0.0    0.0         0.0       0.0   
3202   0.0      0.0     0.0   0.0  0.0      0.0    0.0         0.0       0.0   

      absenc  absolut  absorb  absorpt  abstract  abus  academ  academician  \
0        0.0      0.0     0.0      0.0       0.0   0.0     0.0          0.0   
1        0.0      0.0     0.0      0.0       0.0   0.0     0.0          0.0   
2        0.0      0.0     0.0      0.0       0.0   0.0     0.0          0.0   
3        0.0      0.0     0.0      0.0       0.0   0.0     0.0          0.0   
4        0.0      0.0     0.0      0.0       0.0   0.0     0.0          0.0   
...      ...      ...     ...      ...       ...   ...     ...          ...   
3198     0.0      0.0     0.0      0.0       0.0   0.0     0.0          0.0   
3199     0.0      0.0     0.0      0.0       0.0   0.0     0.0          0.0   
3200     0.0      0.0     0.0      0.0       0.0   0.0     0.0          0.0   
3201     0.0      0.0     0.0      0.0       0.0   0.0     0.0          0.0   
3202     0.0      0.0     0.0      0.0       0.0   0.0     0.0          0.0   

      acceler  accent  accept  access  accid  accident  accommod  accompani  \
0         0.0     0.0     0.0     0.0    0.0       0.0       0.0        0.0   
1         0.0     0.0     0.0     0.0    0.0       0.0       0.0        0.0   
2         0.0     0.0     0.0     0.0    0.0       0.0       0.0        0.0   
3         0.0     0.0     0.0     0.0    0.0       0.0       0.0        0.0   
4         0.0     0.0     0.0     0.0    0.0       0.0       0.0        0.0   
...       ...     ...     ...     ...    ...       ...       ...        ...   
3198      0.0     0.0     0.0     0.0    0.0       0.0       0.0        0.0   
3199      0.0     0.0     0.0     0.0    0.0       0.0       0.0        0.0   
3200      0.0     0.0     0.0     0.0    0.0       0.0       0.0        0.0   
3201      0.0     0.0     0.0     0.0    0.0       0.0       0.0        0.0   
3202      0.0     0.0     0.0     0.0    0.0       0.0       0.0        0.0   

      accomplish  accord  account  accredit  accru  accumul  accur  accuraci  \
0            0.0     0.0      0.0       0.0    0.0      0.0    0.0       0.0   
1            0.0     0.0      0.0       0.0    0.0

Reading queries file

In [16]:
#reading all the queries
# E:\python\cisi_queries
cisi_queries = ""
cisi_queries_file = open('E:\\python\\cisi_queries.txt', 'r')
for line in cisi_queries_file:
    cisi_queries = cisi_queries + line
cisi_queries_corpus = cisi_queries.split('\n')

cacm_queries = ""
cacm_queries_file = open('E:\\python\\cacm_queries.txt', 'r')
for line in cacm_queries_file:
    cacm_queries = cacm_queries + line
cacm_queries_corpus = cacm_queries.split('\n')
# print(cacam_queries_corpus)

In [17]:
cisi_queries = []
cacm_queries = []

In [18]:
def query_to_chunk(chunk,queries_list):
    for sentence in chunk.split('\n'):
        if ".W" in sentence:
            start_index=chunk.find(".W")
            lword=len(".W")
            extracted_string= chunk[start_index:start_index+lword]
            required_string_index = chunk.index(extracted_string)+2
            required_string= chunk[required_string_index:chunk.find(".I") - 2]
            required_string = re.sub('\n',' ',required_string)
            queries_list.append(required_string) 

In [19]:
isThereAnW = True
chunks_list_2 = [' '] * 3000
i = 0
for sentence in cisi_queries_corpus:
#     print(sentence + "\n")
    if ".W" in sentence:
        if isThereAnW:
            chunks_list_2[i]= ' '
            isThereAnW = False
        else:
            query_to_chunk(chunks_list_2[i],cisi_queries)
            i = i + 1
            chunks_list_2[i] = ' '
    chunks_list_2[i] = chunks_list_2[i] + sentence

# print(cisi_queries)

In [20]:
isThereAnW = True
chunks_list_3 = [' '] * 100
i = 0
for sentence in cacm_queries_corpus:
#     print(sentence + "\n")
    if ".W" in sentence:
        if isThereAnW:
            chunks_list_3[i]= ' '
            isThereAnW = False
        else:
            query_to_chunk(chunks_list_3[i],cacm_queries)
            i = i + 1
            chunks_list_2[i] = ' '
    chunks_list_3[i] = chunks_list_3[i] + sentence

# print(cacm_queries)

reading answers

In [21]:
cisi_answers_csv = pd.read_csv("E:\\python\\cisi_answers_csv.csv")
cisi_answers_csv.columns = ['query_id','document_id']
pd.options.display.max_rows = 3100
cisi_answers_csv

query_id  document_id
0            1           28
1            1           35
2            1           38
3            1           42
4            1           43
...        ...          ...
3109       111          422
3110       111          448
3111       111          485
3112       111          503
3113       111          509

[3114 rows x 2 columns]

In [22]:
cisi_answers_dictionary = {}
count = 1
cisi_answers_dictionary[count] = [] 
for i in cisi_answers_csv.values:
    if ((i[0] == count)):
        cisi_answers_dictionary[count].append(i[1])
    else:   
        count = count+1
        cisi_answers_dictionary[count] = [] 
        cisi_answers_dictionary[count].append(i[1])

In [23]:
import pandas as pd
cacm_answers_csv = pd.read_csv("E:\\python\\cacm_answers_csv.csv")
cacm_answers_csv.columns = ['query_id','document_id']
pd.options.display.max_rows = 3100
cacm_answers_csv

query_id  document_id
0           1         1410
1           1         1572
2           1         1605
3           1         2020
4           1         2358
5           2         2434
6           2         2863
7           2         3078
8           3         1134
9           3         1613
10          3         1807
11          3         1947
12          3         2290
13          3         2923
14          4         1749
15          4         1811
16          4         2256
17          4         2371
18          4         2597
19          4         2796
20          4         2912
21          4         3043
22          4         3073
23          4         3082
24          4         3127
25          4         3128
26          5          756
27          5         1307
28          5         1502
29          5         2035
30          5         2299
31          5         2399
32          5         2501
33          5         2820
34          6         1543
35          6         2078
36          6         2828
37          7         1198
38          7         1338
39          7         1877
40          7         1960
41          7         2150
42          7         2228
43          7         2256
44          7         2280
45          7         2320
46          7         2342
47          7         2376
48          7         2482
49          7         2578
50          7         2597
51          7         2618
52          7         2685
53          7         2700
54          7         2777
55          7         2865
56          7         2866
57          7         2895
58          7         2912
59          7         2941
60          7         3043
61          7         3082
62          7         3128
63          7         3141
64          7         3148
65          8         2625
66          8         2849
67          8         3032
68          9         2372
69          9         2632
70          9         2870
71          9         2876
72          9         3068
73          9         3111
74          9         3128
75          9         3158
76          9         3177
77         10           46
78         10          141
79         10          392
80         10          950
81         10         1158
82         10         1198
83         10         1262
84         10         1380
85         10         1471
86         10         1601
87         10         1613
88         10         1747
89         10         1795
90         10         1811
91         10         2060
92         10         2150
93         10         2256
94         10         2289
95         10         2342
96         10         2376
97         10         2433
98         10         2618
99         10         2664
100        10         2685
101        10         2700
102        10         2714
103        10         2777
104        10         2785
105        10         2851
106        10         2895
107        10         2896
108        10         2912
109        10         3039
110        10         3075
111        10         3156
112        11         1043
113        11         1188
114        11         1306
115        11         1358
116        11         1396
117        11         1491
118        11         1923
119        11         2246
120        11         2316
121        11         2527
122        11         2699
123        11         2710
124        11         2715
125        11         2716
126        11         2906
127        11         2923
128        11         2956
129        11         3073
130        11         3150
131        12         1523
132        12         2080
133        12         2246
134        12         2629
135        12         3127
136        13          115
137        13         1223
138        13         1231
139        13         1551
140        13         1625
141        13         1795
142        13         1807
143        13         1947
144        13         2495
145        13         2579
146        13         2897
147      

In [24]:
cacm_answers_dictionary = {}
count = 1
cacm_answers_dictionary[count] = [] 
for i in cacm_answers_csv.values:
    if ((i[0] == count)):
        cacm_answers_dictionary[count].append(i[1])
    else:   
        count = count+1
        cacm_answers_dictionary[count] = [] 
        cacm_answers_dictionary[count].append(i[1])

matching function
and vectorization queries and documents

In [25]:
cx = lambda a, b : np.dot(a, b)/(np.linalg.norm(a)*np.linalg.norm(b))

In [26]:
def matching_function(corpus,queries,answers):
    output = {}
    vectorizer = TfidfVectorizer()
    train_set = corpus #Documents
    test_set = queries
    new_test_set = []
    for test in test_set:
        test = clean_text_round1(test)
        test = clean_text_round2(test)
        test = clean_text_round3(test)
        test = clean_text_round5(test)
        test = clean_text_round6(test)
        test = clean_text_round7(test)
        new_test_set.append(test)        
    trainVectorizerArray = vectorizer.fit_transform(train_set).toarray()
    testVectorizerArray = vectorizer.transform(new_test_set).toarray()
    i = 1;
    for testV in testVectorizerArray:
        d_cosines = []
        for vector in trainVectorizerArray:
            cosine = cx(vector, testV)
            d_cosines.append(cx(vector, testV))
        number = len(answers.get(i))
        out = np.array(d_cosines).argsort()[-number:][::-1]
        output[i] = out
        if(i < len(answers)):
            i = i+1

    for out in output:
        output[out].sort()

    for out in output:
        i = 0
        for num in output[out]:
            output[out][i] = num+1
            i = i + 1
    return output

calculate presicion and recall and f1_score for all queries

In [27]:

def calculate_measures(true_answers,test_answers,document_size):
    accurecy_measures = {'true_answers':[],'test_answers':[],'precision':[],'recall':[]}
    counter = 1
    for true_answer,test_answer in zip(true_answers,test_answers):
#         print(counter)
        accurecy_measures[ 'true_answers'].append(counter)
        accurecy_measures['test_answers'].append(counter)
        arr_1 = [0] * document_size
        k = 0
        for i in arr_1:
            for j in true_answer:
                if k == j:
                    arr_1.insert(j, 1)
            k = k+1
        arr_2 = [0] * document_size
        m = 0
        for i in arr_2:
            for j in test_answer:
                if m == j:
                    arr_2.insert(j, 1)
            m = m+1
        
        precision = precision_score(arr_1,arr_2, average='macro',zero_division='warn')
        accurecy_measures['precision'].append(precision)

        recall = recall_score(arr_1,arr_2, average='weighted')
        accurecy_measures['recall'].append(recall)
               
        counter = counter+1
    return accurecy_measures

In [46]:
def caculate_mrr(results,truths):
    MAX_RANK = 1000
    ranked_table = {'query_id':[],'document_id':[],'rank':[]} 
    answers_table = {'query_id':[],'document_id':[]}
    for row in results:
        temp_list = results[row]
        i = 1
        for num in temp_list:
            ranked_table['query_id'].append(row)
            ranked_table['document_id'].append(num)
            ranked_table['rank'].append(i)
            i = i+1
    ranked_df = pd.DataFrame(ranked_table)
    
    for row in truths:
        temp_list = truths[row]
        for num in temp_list:
            answers_table['query_id'].append(row)
            answers_table['document_id'].append(num)
    truths_df = pd.DataFrame(answers_table)

    hits = pd.merge(truths_df, ranked_df,
        on=["query_id", "document_id"],
        how="left").fillna(MAX_RANK)
    mrr = (1 / hits.groupby('query_id')['rank'].min()).mean()
    return mrr

In [48]:
cisi_queries_result = matching_function(cisi_df.content,cisi_queries,cisi_answers_dictionary)
cisi_accurecy_measures = calculate_measures(cisi_answers_dictionary.values() , cisi_queries_result.values(),1500)
cisi_accurecy_measures_df = pd.DataFrame(cisi_accurecy_measures)
cisi_accurecy_measures_df

<ipython-input-43-d5382450dcdb>:1: RuntimeWarning: invalid value encountered in double_scalars
  cx = lambda a, b : np.dot(a, b)/(np.linalg.norm(a)*np.linalg.norm(b))


true_answers  test_answers  precision    recall
0               1             1   0.753536  0.971539
1               2             2   0.530462  0.968545
2               3             3   0.695879  0.966321
3               4             4   0.497333  0.989390
4               5             5   0.534333  0.971129
5               6             6   0.499667  0.998668
6               7             7   0.497333  0.989390
7               8             8   0.494000  0.976285
8               9             9   0.593941  0.964798
9              10            10   0.569590  0.971166
10             11            11   0.607129  0.886908
11             12            12   0.573256  0.985459
12             13            13   0.627018  0.919547
13             14            14   0.499000  0.996008
14             15            15   0.627008  0.926675
15             16            16   0.589154  0.972477
16             17            17   0.510897  0.967235
17             18            18   0.633697  0.989411
18             19            19   0.629148  0.927894
19             20            20   0.562361  0.860097
20             21            21   0.552667  0.971148
21             22            22   0.540937  0.939472
22             23            23   0.570000  0.948320
23             24            24   0.621949  0.951031
24             25            25   0.643848  0.969993
25             26            26   0.712881  0.960154
26             27            27   0.630188  0.902167
27             28            28   0.601333  0.941026
28             29            29   0.613000  0.953488
29             30            30   0.695149  0.908201
30             31            31   0.582027  0.937220
31             32            32   0.622239  0.898578
32             33            33   0.518667  0.975000
33             34            34   0.635737  0.964889
34             35            35   0.605279  0.957226
35             36            36   0.499667  0.998668
36             37            37   0.605385  0.961014
37             38            38   0.499667  0.998668
38             39            39   0.553824  0.980224
39             40            40   0.499667  0.998668
40             41            41   0.698000  0.992053
41             42            42   0.617667  0.952258
42             43            43   0.534462  0.984137
43             44            44   0.644086  0.879154
44             45            45   0.576736  0.921370
45             46            46   0.647080  0.905941
46             47            47   0.499667  0.998668
47             48            48   0.499667  0.998668
48             49            49   0.601042  0.967363
49             50            50   0.744094  0.945878
50             51            51   0.499667  0.998668
51             52            52   0.531381  0.982827
52             53            53   0.499667  0.998668
53             54            54   0.628000  0.953548
54             55            55   0.494000  0.976285
55             56            56   0.542222  0.948220
56             57            57   0.550222  0.978920
57             58            58   0.540681  0.946960
58             59            59   0.499667  0.998668
59             60            60   0.499667  0.998668
60             61            61   0.497000  0.988072
61             62            62   0.748000  0.992063
62             63            63   0.499667  0.998668
63             64            64   0.499667  0.998668
64             65            65   0.771061  0.993382
65             66            66   0.707619  0.973941
66             67            67   0.585083  0.966057
67             68            68   0.499667  0.998668
68             69            69   0.639524  0.986790
69             70            70   0.499667  0.998668
70             71            71   0.491333  0.965924
71             72            72   0.499667  0.998668
72             73            73   0.499667  0.998668
73             74            74   0.499667  0.998668
74             75            7

In [49]:
precision_average = sum(cisi_accurecy_measures_df.precision) / len(cisi_accurecy_measures_df.precision)
print("precision_average")
print(precision_average)
recall_average = sum(cisi_accurecy_measures_df.recall) / len(cisi_accurecy_measures_df.recall)
print("\n recall_average")
print(recall_average)
mrr = caculate_mrr(cisi_queries_result,cisi_answers_dictionary)
print("\n mrr")
print(mrr)

precision_average
0.5526570176005151

 recall_average
0.9726117123817167

 mrr
0.2661387648152359


In [50]:
cacm_queries_result = matching_function(cacm_df.content,cacm_queries,cacm_answers_dictionary)
cacm_accurecy_measures = calculate_measures(cacm_answers_dictionary.values() , cacm_queries_result.values(),3300)
cacm_accurecy_measures_df = pd.DataFrame(cacm_accurecy_measures)
cacm_accurecy_measures_df

true_answers  test_answers  precision    recall
0              1             1   0.599394  0.997579
1              2             2   0.499545  0.998183
2              3             3   0.582576  0.996975
3              4             4   0.581818  0.993961
4              5             5   0.624091  0.996372
5              6             6   0.666364  0.998789
6              7             7   0.675844  0.989183
7              8             8   0.499545  0.998183
8              9             9   0.721465  0.996978
9             10            10   0.841190  0.993403
10            11            11   0.708860  0.993371
11            12            12   0.699545  0.998185
12            13            13   0.635152  0.995168
13            14            14   0.815758  0.990431
14            15            15   0.598788  0.995166
15            16            16   0.556551  0.990956
16            17            17   0.591780  0.992159
17            18            18   0.635152  0.995168
18            19            19   0.726364  0.996376
19            20            20   0.499545  0.998183
20            21            21   0.543939  0.993960
21            22            22   0.793057  0.995779
22            23            23   0.499394  0.997579
23            24            24   0.613869  0.993963
24            25            25   0.671471  0.980304
25            26            26   0.730909  0.990390
26            27            27   0.721714  0.990388
27            28            28   0.899848  0.999395
28            29            29   0.788262  0.995179
29            30            30   0.624545  0.998184
30            31            31   0.749848  0.999394
31            32            32   0.666364  0.998789
32            33            33   0.499848  0.999394
33            34            34   0.499848  0.999394
34            35            35   0.499848  0.999394
35            36            36   0.497273  0.989150
36            37            37   0.498182  0.992754
37            38            38   0.497576  0.990350
38            39            39   0.623636  0.994565
39            40            40   0.849545  0.998187
40            41            41   0.499848  0.999394
41            42            42   0.496970  0.987952
42            43            43   0.493788  0.975456
43            44            44   0.497424  0.989750
44            45            45   0.496061  0.984366
45            46            46   0.499848  0.999394
46            47            47   0.499848  0.999394
47            48            48   0.498485  0.993958
48            49            49   0.498788  0.995163
49            50            50   0.499848  0.999394
50            51            51   0.499848  0.999394
51            52            52   0.499848  0.999394
52            53            53   0.499848  0.999394
53            54            54   0.499848  0.999394
54            55            55   0.499848  0.999394
55            56            56   0.499848  0.999394
56            57            57   0.499848  0.999394
57            58            58   0.496515  0.986157
58            59            59   0.493485  0.974275
59            60            60   0.495909  0.983769
60            61            61   0.560425  0.983789
61            62            62   0.498788  0.995163
62            63            63   0.498182  0.992754
63            64            64   0.499848  0.999394

In [51]:
precision_average = sum(cacm_accurecy_measures_df.precision) / len(cacm_accurecy_measures_df.precision)
precision_average

0.5867391528009778

request a query function

In [28]:
from sklearn.feature_extraction.text import TfidfTransformer
# print(len(trainVectorizerArray))
 #Documents

def query_documents(corpus_id,query_id):
    train_set = cisi_df.content
    documents = []
    answers_dictionary = cisi_answers_dictionary
    vectorizer = CountVectorizer(stopwords)
    transformer = TfidfTransformer()
    new_test = []
    if(corpus_id == 1):
        train_set = list(cisi_df.content)
        answers_dictionary = cisi_answers_dictionary
        
    if(corpus_id == 2):
        train_set = cacm_df.content
        answers_dictionary = cacm_answers_dictionary  
    
    test = search_for_query(query_id,corpus_id)
    print(test)
    test = clean_text_round1(test)
    test = clean_text_round2(test)
    test = clean_text_round3(test)
    test = clean_text_round4(test)
    test = clean_text_round5(test)
    test = clean_text_round6(test)
    test = clean_text_round7(test)
    new_test.append(test)  
    
    trainVectorizerArray = vectorizer.fit_transform(train_set).toarray()
    testVectorizerArray = vectorizer.transform(new_test).toarray()
    
    d_cosines = []
    for vector in trainVectorizerArray:
        for testV in testVectorizerArray:
            cosine = cx(vector, testV)
            d_cosines.append(cx(vector, testV))
        
    transformer.fit(trainVectorizerArray)
    number = len(answers_dictionary.get(query_id+1))
    out = np.array(d_cosines).argsort()[-number:][::-1]
    out.sort()
    i = 0
    for num  in out:
        out[i] = num+1
        i = i+1
    for num in out:
        documents.append(num)
    
    result = {'title': [],'body':[]}
    for num in documents:
        result['title'].append(num)
        result['body'].append(cisi_df.content.loc[num-1])
    
    return result

In [29]:
def search_for_query(query_id,queries_document_id):
    if(queries_document_id == 1):
        return cisi_queries[query_id]
    else:
        return cacm_queries[query_id]

In [32]:
answers = query_documents(1,0)
answers
d = pd.DataFrame(answers)
d

C:\Users\dell\anaconda3\lib\site-packages\sklearn\utils\validation.py:70: FutureWarning: Pass input=<WordListCorpusReader in 'C:\\Users\\dell\\AppData\\Roaming\\nltk_data\\corpora\\stopwords'> as keyword args. From version 1.0 (renaming of 0.25) passing these as positional arguments will result in an error
  warnings.warn(f"Pass {args_msg} as keyword args. From version "


What problems and concerns are there in making up descriptive titles?What difficulties are involved in automatically retrieving articles fromapproximate titles?What is the usual relevance of the content of articles to their title


title  \
0      17   
1      38   
2      42   
3      52   
4      65   
5      76   
6     110   
7     176   
8     219   
9     269   
10    276   
11    429   
12    447   
13    449   
14    465   
15    466   
16    510   
17    541   
18    582   
19    589   
20    603   
21    620   
22    650   
23    711   
24    722   
25    759   
26    783   
27    784   
28    813   
29    820   
30    836   
31    851   
32    868   
33    895   
34    958   
35   1000   
36   1009   
37   1064   
38   1090   
39   1091   
40   1177   
41   1196   
42   1265   
43   1281   
44   1299   
45   1364   

                                                                                                   body  
0   adventur librarianship voigt one thousand , nine hundr and seventi long need continu seri provid...  
1   machinelik index peopl montgomeri swanson studi thousand entri classifi bibliographi articl titl...  
2   notion relev hillman donald analysi problem defin mutual relev queri document collect essenti in...  
3   compar index term suppli biomed author document titl schultz clair schultz wallac orr richard or...  
4   studi search eye research literatur miller russel paper report major find studi search period ey...  
5   biomed literatur analysi journal articl collect radiat cell biologist leith john jr author journ...  
6   gatekeep scienc factor affect select articl scientif journal crane norm scientif behavior merton...  
7   autom keyword classif inform retriev sparck jone book primarili research monograph discuss main ...  
8   select list journal small medic librari compar analysi timour john result survey weight summari ...  
9   sampl short period usag purdu librari jain method sampl social scienc monograph titl gener libra...  
10  titl catalog dimens nitecki joseph access card catalog invers proport complex arrang catalog div...  
11  inform content titl engin literatur bottl robert alert inform servic reli heavili titl transfer ...  
12  note concept relev foskett recent articl journal konigova two million , twenty-two thousand and ...  
13  situat relev wilson patrick concept situat relev introduc base cooper definit logic relev notion...  
14  commerci literatur tap awar servic corbett paper review need awar servic describ basic character...  
15  univers sheffield biomed inform project barkla outlin histori project develop osti support infor...  
16  retriev effici titl cost index tell bjorn mean flexibl machin search system experi make order te...  
17  isbd titl main entri serial spald sumner ifla liverpool confer one thousand , nine hundr and sev...  
18  titl index alert servic chemic life scienc bottl robert principl underli alert servic discu gene...  
19  titl chemic paper inform tocatlian jacqu effici key work context kwic permut titl index numer va...  
20  effici medlar titl retriev miller william previou research titl index term standard medlar syste...  
21  line serial control system larg biomed librari part ii evalu retriev featur fayollat jam line se...  
22  rel effect titl abstract subject head machin retriev compendex servic byrn jerri investig rel me...  
23  develop product chemic titl awar index public prepar aid comput freeman dysn introduct chemic ti...  
24  inform transfer limit titl chemic document bottl seeley method estim minimum amount inform docum...  
25  look refer scatter cole observ bradford larg collect journal refer subject articl deriv small pr...  
26  author versu titl compar survey accuraci inform user bring librari catalogu ayr german janic lou...  
27  document note cawkel suggest reason constant averag number refer articl firstli averag articl fi...  
28  compar effici search titl abstract term free text data base barcer veal wyatt choic suitabl data...  
29  studi compar retriev titl index term sdi nuclear scienc abstract oliv terri datta select dissemi...  
30  entri titl compress code access machin readabl bibliograph newman william buchinski edwin entri ...  


Word Embedding

In [69]:
nlp = spacy.load("en_core_web_sm")
from nltk import pos_tag
def extract_names_and_adjectives(text):
    is_noun_or_adj = lambda pos: pos[:2] == 'NN' or pos[:2] == 'JJ'
    tokenized = word_tokenize(text)
    nouns_and_adjs = [word for(word,pos) in pos_tag(tokenized) if is_noun_or_adj(pos)]
    return ' '.join(nouns_and_adjs)
nouns_adjs= lambda x: extract_names_and_adjectives(x)

In [70]:
def delete_numbers(text):
    new_text = ''
    words = word_tokenize(text)
    for w in words:
        if w.isnumeric():
            w = ' '
        new_text += w + ' '   
    return new_text
del_numbers = lambda x: delete_numbers(x)

In [71]:
def delete_dates(text):
    text = sent_tokenize(text)
    required_text = ""
    for sentence in text:
        matches = datefinder.find_dates(sentence,source = True)
        try:
            if matches is not None:
                for match in matches:
                    temp_date = match[1]
                    sentence = sentence.replace(temp_date," ",1)
        except:
            print("error with date")
        required_text = required_text + sentence
    return required_text
del_dates = lambda x: delete_dates(x)

In [72]:
cisi_queries_list = []
cisi_queries_word_embedding_vectors = []

for test in cisi_queries:
    test = clean_text_round1(test)
    test = clean_text_round2(test)
    test = delete_dates(test)
    test = delete_numbers(test)
    test = clean_text_round5(test)
    test = clean_text_round7(test)
    test = extract_names_and_adjectives(test)
    cisi_queries_list.append(test)
print(len(cisi_queries_list))

for query in cisi_queries_list:
    cisi_queries_word_embedding_vectors.append(nlp(query).vector)

error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
error with date
112


In [73]:
# cisi_df.content = cisi_df.content.apply(round1)
cisi_df.content = cisi_df.content.apply(round2)
cisi_df.content = cisi_df.content.apply(del_dates)
cisi_df.content  = cisi_df.content.apply(del_numbers)
print("start with round5")
cisi_df.content = cisi_df.content.apply(round5)
print("start with round7")
cisi_df.content = cisi_df.content.apply(round7)
print("start vectorization")
cisi_corpus_word_embedding_vectors = [nlp(content).vector for content in cisi_df.content]

start with round5
start with round7
start vectorization


In [63]:
len(cisi_queries_word_embedding_vectors)

112

In [64]:
len(cisi_corpus_word_embedding_vectors)

1460

In [75]:
from sklearn.metrics.pairwise import cosine_similarity

documents = []
output = {}
i = 1;

for testV in cisi_queries_word_embedding_vectors:
    d_cosines = []
    try:
        for vector in cisi_corpus_word_embedding_vectors:
            cosine = cx(vector, testV)
            d_cosines.append(cx(vector, testV))
    except:
        number = len(cisi_answers_dictionary.get(i))
        d_cosines = [0] * number
        output[i] = d_cosines
        print("an error occured")
    number = len(cisi_answers_dictionary.get(i))
    out = np.array(d_cosines).argsort()[-number:][::-1]
    output[i] = out
    if(i < len(cisi_answers_dictionary)):
        i = i+1

for out in output:
    output[out].sort()

for out in output:
    i = 0
    for num in output[out]:
        output[out][i] = num+1
        i = i + 1

an error occured
an error occured


In [101]:
# after_word_embedding = calculate_measures(cisi_answers_dictionary.values() , output.values(),1500)
i = 1
for p in after_word_embedding['precision']:
    print(after_word_embedding['precision'])
    i = i + 1
# after_word_embedding
# after_word_embedding_df = pd.DataFrame(after_word_embedding)
# after_word_embedding_df
# after_word_embedding['precision']

TypeError: 'numpy.float64' object is not iterable

In [103]:
precision_average = sum(after_word_embedding_df.precision) / len(after_word_embedding_df.precision)
print("precision_average")
print(precision_average)
recall_average = sum(after_word_embedding_df.recall) / len(after_word_embedding_df.recall)
print("\n recall_average")
print(recall_average)
mrr = caculate_mrr(output,cisi_answers_dictionary) 
print("\n mrr")
print(mrr)

precision_average
0.713511588999546

 recall_average
0.9676090278261437

 mrr
0.1364556129385349


In [221]:
final_result = {}
def adding_word_embedding_to_total_work(num_of_queries,before_embedding_list,after_embedding_list,answers_dictionary):
    i  = 1
    while i < num_of_queries:
#         print(i)
        initial = []
        final = []
        query_num_of_answers = answers_dictionary[i]
#         print(len(query_num_of_answers))
        initial = set(before_embedding_list[i]).intersection(after_embedding_list[i])
        final = list(initial)
        if(len(final) > len(query_num_of_answers)):
            final = final[-len(query_num_of_answers):]
        if(len(final) != query_num_of_answers):
            for num in after_embedding_list[i]:
                if((num not in initial) & (len(final) < len(query_num_of_answers))):
                     final.append(num)
#         print(len(final))
        final_result[i] = final
        i = i+1
    return final_result

In [222]:
cacm_queries_resul_2 = matching_function_2(cisi_df.content,cisi_queries,cisi_answers_dictionary)

<ipython-input-23-d5382450dcdb>:1: RuntimeWarning: invalid value encountered in double_scalars
  cx = lambda a, b : np.dot(a, b)/(np.linalg.norm(a)*np.linalg.norm(b))


In [223]:
# print(len(final_result))
final_result = adding_word_embedding_to_total_work(len(cisi_queries),cacm_queries_resul_2,output_2,cisi_answers_dictionary)


In [224]:
# cisi_queries_result_2 = matching_function(cisi_df.content,cisi_queries,cisi_answers_dictionary)
cisi_accurecy_measures_2 = calculate_measures(cisi_answers_dictionary.values() , final_result.values(),1500)
cisi_accurecy_measures_df_2 = pd.DataFrame(cisi_accurecy_measures_2)
precision_average = sum(cisi_accurecy_measures_df_2.precision) / len(cisi_accurecy_measures_df_2.precision)
print(precision_average)
cisi_accurecy_measures_df_2


0.5165935420898052


true_answers  test_answers  precision    recall
0               1             1   0.507072  0.943079
1               2             2   0.491333  0.965924
2               3             3   0.614000  0.957254
3               4             4   0.560167  0.990716
4               5             5   0.513167  0.969816
5               6             6   0.499667  0.998668
6               7             7   0.497333  0.989390
7               8             8   0.494000  0.976285
8               9             9   0.503706  0.956975
9              10            10   0.530462  0.968545
10             11            11   0.530262  0.864782
11             12            12   0.495667  0.982816
12             13            13   0.522117  0.896920
13             14            14   0.499000  0.996008
14             15            15   0.569130  0.915297
15             16            16   0.530462  0.968545
16             17            17   0.491333  0.965924
17             18            18   0.542121  0.986764
18             19            19   0.525049  0.907653
19             20            20   0.543333  0.854015
20             21            21   0.491667  0.967213
21             22            22   0.501868  0.934321
22             23            23   0.516250  0.941860
23             24            24   0.492615  0.934278
24             25            25   0.489000  0.956947
25             26            26   0.638786  0.949871
26             27            27   0.588058  0.891022
27             28            28   0.506000  0.926923
28             29            29   0.570000  0.948320
29             30            30   0.540692  0.861689
30             31            31   0.513787  0.926970
31             32            32   0.571564  0.884972
32             33            33   0.493333  0.973684
33             34            34   0.527807  0.954486
34             35            35   0.509589  0.946857
35             36            36   0.499667  0.998668
36             37            37   0.526462  0.953216
37             38            38   0.499667  0.998668
38             39            39   0.524078  0.978906
39             40            40   0.499667  0.998668
40             41            41   0.547000  0.988079
41             42            42   0.483333  0.935484
42             43            43   0.534462  0.984137
43             44            44   0.551548  0.847734
44             45            45   0.508468  0.908687
45             46            46   0.498483  0.866337
46             47            47   0.499667  0.998668
47             48            48   0.499667  0.998668
48             49            49   0.537208  0.962141
49             50            50   0.583408  0.911894
50             51            51   0.499667  0.998668
51             52            52   0.495333  0.981506
52             53            53   0.499667  0.998668
53             54            54   0.514333  0.939355
54             55            55   0.550222  0.978920
55             56            56   0.507889  0.944337
56             57            57   0.522111  0.977602
57             58            58   0.495870  0.941785
58             59            59   0.499667  0.998668
59             60            60   0.499667  0.998668
60             61            61   0.497000  0.988072
61             62            62   0.496000  0.984127
62             63            63   0.499667  0.998668
63             64            64   0.499667  0.998668
64             65            65   0.587909  0.988087
65             66            66   0.546810  0.959609
66             67            67   0.505292  0.959530
67             68            68   0.499667  0.998668
68             69            69   0.531381  0.982827
69             70            70   0.499667  0.998668
70             71            71   0.530462  0.968545
71             72            72   0.499667  0.998668
72             73            73   0.499667  0.998668
73             74            74   0.499667  0.998668
74             75            7

Topic Detection

In [16]:
from nltk import pos_tag
def extract_names_and_adjectives(text):
    is_noun_or_adj = lambda pos: pos[:2] == 'NN' or pos[:2] == 'JJ'
    tokenized = word_tokenize(text)
    nouns_and_adjs = [word for(word,pos) in pos_tag(tokenized) if is_noun_or_adj(pos)]
    return ' '.join(nouns_and_adjs)
nouns_adjs= lambda x: extract_names_and_adjectives(x)

In [25]:
#Create Dictionary
cisi_df.content = cisi_df.content.apply(round2)
cisi_df.content = cisi_df.content.apply(round5)
cisi_df.content = cisi_df.content.apply(nouns_adjs)

arr = []
for sentence in cisi_df.content:
    arr.append(sentence)
dataset = [d.split() for d in arr]

id2word = corpora.Dictionary(dataset)
# print(id2word)

#create corpus
texts = dataset

# Term Document Frequency 
c = [id2word.doc2bow(text) for text in texts]  

In [29]:
lda_model = gensim.models.ldamodel.LdaModel(corpus=c,
                                           id2word=id2word,
                                           num_topics=12, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=30,
                                           alpha='auto',
                                           per_word_topics=True)

In [30]:
# Print the keyword of topics
pprint(lda_model.print_topics())
doc_lda = lda_model[c]
print(doc_lda)

[(0,
  '0.082*"text" + 0.080*"automatic" + 0.055*"word" + 0.044*"thesaurus" + '
  '0.037*"vocabulary" + 0.037*"language" + 0.023*"construction" + '
  '0.014*"positive" + 0.012*"cent" + 0.012*"experiment"'),
 (1,
  '0.194*"library" + 0.059*"book" + 0.027*"university" + 0.025*"librarian" + '
  '0.019*"material" + 0.018*"survey" + 0.016*"collection" + 0.013*"school" + '
  '0.012*"education" + 0.012*"reader"'),
 (2,
  '0.089*"index" + 0.052*"chemical" + 0.051*"abstract" + 0.049*"title" + '
  '0.040*"search" + 0.040*"term" + 0.020*"profile" + 0.019*"notation" + '
  '0.018*"compound" + 0.016*"dictionary"'),
 (3,
  '0.030*"theory" + 0.025*"term" + 0.025*"analysis" + 0.023*"structure" + '
  '0.021*"citation" + 0.019*"language" + 0.018*"author" + 0.017*"model" + '
  '0.017*"measure" + 0.016*"method"'),
 (4,
  '0.046*"growth" + 0.041*"rule" + 0.024*"rate" + 0.024*"machine" + '
  '0.023*"standard" + 0.022*"marc" + 0.021*"processing" + 0.018*"output" + '
  '0.016*"entry" + 0.015*"business"'),
 (5,

In [19]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(c))  
# a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=dataset, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)

# Lower the perplexity better the model.
# Higher the topic coherence, the topic is more human interpretable.


Perplexity:  -8.38038477467888

Coherence Score:  0.42489034255016306


In [ ]:
bow_corpus = [dictionary.doc2bow(text) for text in processed_corpus]
pprint.pprint(bow_corpus)

In [31]:
from gensim import models

# train the model
tfidf = models.TfidfModel(c)

# transform the "system minors" string
words = "semantic norm".lower().split()
# print(tfidf[dictionary.doc2bow(words)])
print(tfidf[id2word.doc2bow(words)])

[(705, 0.8206669022032452), (2672, 0.5714068914776311)]


In [25]:
c[:1]

[[(0, 1),
  (1, 1),
  (2, 1),
  (3, 2),
  (4, 1),
  (5, 1),
  (6, 1),
  (7, 2),
  (8, 2),
  (9, 1),
  (10, 1),
  (11, 3),
  (12, 4),
  (13, 1),
  (14, 1),
  (15, 1),
  (16, 1),
  (17, 1),
  (18, 2),
  (19, 1),
  (20, 1),
  (21, 1),
  (22, 1),
  (23, 1),
  (24, 1),
  (25, 1),
  (26, 1)]]

In [1]:
from gensim import similarities

index = similarities.SparseMatrixSimilarity(tfidf[c[:1]], num_features=12)

NameError: name 'tfidf' is not defined

In [ ]:
# df2 = pd.DataFrame(index)
# df2

In [27]:
query_document = 'system engineering'.split()

In [28]:
query_bow = id2word.doc2bow(query_document)

In [ ]:
index[tfidf[query_bow]]

In [ ]:
print(list(enumerate(sims)))